# Web Scraping Used Cars on sgcarmart.com
## 1. Introduction

### This document outlines the process of web scraping data from sgcarmart.com, the largest online car marketplace in Singapore, to analyze the used car market.

### Respecting sgcarmart.com's Rules
The scraping script will adhere to the guidelines outlined in sgcarmart.com's robots.txt file. Here's a summary of the restrictions:

Crawlers must wait at least 5 seconds between requests (Crawl-delay: 5).
Specific directories are off-limits for scraping, including:
cgi-bin/
images/
mail/
dealer/
directory/premium/
includes/
phpads/
update/
upload/

### Data Extraction
The script will focus on extracting the following information for each used car listing:

Car Listing URL 'LISTING_URL', 
Car Brand and Model 'BRAND', 
Price 'PRICE', 
Depreciation Value Yearly 'DEPRE_YEARLY', 
Registered Date 'REG_DATE', 
Mileage in KM 'MILEAGE_KM', 
Year of Manufacture 'MANUFACTURED_YEAR', 
Road Tax Yearly 'ROAD_TAX_YEARLY', 
Automatic or Manual Tranmission 'TRANSMISSION', 
Deregistration Value as of Web Scraping DTD 'DEREG_VALUE_FROM_SCRAPE_DATE', 
Web Scraping DTD 'SCRAPE_DATE', 
Open Market Value (OMV) 'OMV', 
Additional Registration Fee (ARF) 'ARF', 
Certificate of Entitlement (COE) from Web Scraping DTD 'COE_FROM_SCRAPE_DATE', 
Number of Days till COE Expires 'DAYS_OF_COE_LEFT', 
Engine Capacity in CC 'ENGINE_CAPACITY_CC', 
Car Curb Weight in KG 'CURB_WEIGHT_KG', 
Number of Past Owners 'NO_OF_OWNERS', 
Vehicle Type 'VEHICLE_TYPE'

This data will be used for further analysis of the used car market in Singapore.

## 2. Import Libraries

In [11]:
from bs4 import BeautifulSoup
import requests
import pandas as pd
import numpy as np
import time
import re
from datetime import datetime

## 3. Pre-defined Functions

In [12]:
# A set of functions is defined to extract specific attributes from a parsed individual car listing URL, with each function returning the corresponding attribute.


# Brand Retriever Function 
 
def brand_retrieval(parsed_url):
    # Locate the anchor element (<a>) within the parsed URL that has the class attribute "nounderline globaltitle"
    brand_tag = parsed_url.find("a", class_="nounderline globaltitle")
    
    if brand_tag:
        # Retrieve the brand name from the href attribute of the identified anchor element. The brand name is encoded as a URL-encoded string and requires decoding
        brand_name = brand_tag["href"].split("=")[1].replace("+", " ").split("&")[0]
        return brand_name
    else:
        brand_name = np.nan  # Stores NA values as nan
    
    return brand_name
    
# Price Retriever Function

def price_error_handler(data_value):
    # Implement exception handling using the try-except block to handle potential errors during price extraction
    
    try:   # Initially attempt to extract the price from the second element of the data_value list. 
           # If successful, convert the price string into an integer by concatenating the parts separated by commas
        price = data_value[1]  # The code will raise an IndexError if the data_value list does not contain at least two element
        price = int(price.split(',')[0] + price.split(',')[1]) # The code will raise an IndexError if the price string cannot be split into two parts separated by a comma
        
    except IndexError:  # Handle the cases where the data_value list is missing elements or contains unexpected values
        try: 
            price = int(data_value[1]) # The code will raise an IndexError if the data_value list does not contain at least two elements
        except IndexError:  # Deals with ['na'] scenarios
            price = np.nan  # Stores NA values as nan
    
    return price

def price_retrieval(parsed_listing_url):
    
    data_value = parsed_listing_url.find_all(class_="font_red")[0].text.strip()
    data_value = data_value.split('$')
    price = price_error_handler(data_value)
    return price

# Deprecration Value Per Year Retriever Function
def depreciation_yearly_error_handler(data_value):
    if len(data_value) < 2:
        data_value = np.nan

    else: 
        data_value = data_value[1].split('/yr')
        try:                 
            desired_value = int(data_value[0].split(',')[0] +\
                                data_value[0].split(',')[1]) # Will fail on IndexError if tries to split '900' with a ',' in ['900','']
        except IndexError: 
            desired_value = int(data_value[0])
        
        return desired_value
    
def depreciation_yearly_retrieval(parsed_listing_url):
    data_value = parsed_listing_url.find_all(class_="label")[1].findNextSibling().text.strip().split('$')
    depreciation_yearly = depreciation_yearly_error_handler(data_value)
    return depreciation_yearly

# Road Tax Per Year Retriever
def road_tax_error_handler(string_data):
    if '/yr' in string_data: # Only takes in scenarios that are not NA
        try:
            # Removes '$" character and splits string_data into a list of ['', 1,000] or ['', 900]
            road_tax_yearly = \
            string_data.replace('/yr','').strip().split('$') 

            # Accesses the second item in the list
            road_tax_yearly = road_tax_yearly[1] 


            road_tax_yearly = int(road_tax_yearly.split(',')[0] +\
                                    road_tax_yearly.split(',')[1])  # Will fail on IndexError if value is above 1000

        except IndexError: # Handles values that are below 1000. (i.e. ['',900])
            road_tax_pear_year = int(road_tax_yearly[1])

    else: # Deals with 'NA' scenario
        road_tax_yearly = np.nan
    
    return road_tax_yearly

def road_tax_retrieval(parsed_listing_url):
    string_data = parsed_listing_url.find_all(class_='row_info')[1].text.strip()
    road_tax_yearly = road_tax_error_handler(string_data)
    
    return road_tax_yearly
    

# Registered Date Retriever
def reg_date_retrieval(parsed_listing_url):
    reg_date = parsed_listing_url.find_all(class_='row_bg')[1].find_all('td')[3].text.split()[0].split('(')[0]
    return reg_date

# Days of COE Retriever
def days_of_coe_retrieval(parsed_listing_url):
    days_of_coe_left_yy_mm_dd_format_for_cleaner_function=\
    parsed_listing_url.find_all(class_='row_bg')[1].find_all('td')[3].text.split('(')[1].split('COE')[0].strip()
    
    return yr_mm_dd_cleaner(days_of_coe_left_yy_mm_dd_format_for_cleaner_function)


# Define a function to calculate days of COE left
def yr_mm_dd_cleaner(str1):
    """Accepts a string that may or may include the elements yr mths days and 
    converts the whole string into number of days.
    ----
    Input: single string
    output: number of days in integer form
    ----
    Example string inputs:
    - 4yrs 2mths 23days
    - 5yrs
    - 2 mths 23 days
    - 50 days
    """
    
    # Convert days_of_coe_left_yy_mm_dd to days    
    year_index = str1.find('yr')
    if year_index == -1:
        year = 0
    else:
        year = int(str1[year_index-1])

        
    mth_index = str1.find('mth')
    if mth_index == -1:
        mth = 0
    else:
        mth = int(str1[mth_index-1])

        
    day_index = str1.find('day')
    if day_index == -1:
        day = 0
    else:
        day = int(str1[day_index-1])
       
    days_of_coe_left = (year * 365) + (mth * 30) + day 
    return days_of_coe_left


# Mileage Retriever
def mileage_error_handler(data_value):
    if len(data_value) < 2:  # Deals with ['na'] scenarios
        mileage_km = np.nan  # Stores NA values as nan

    else:  
        try:                 
            mileage_km = int(data_value[0].strip().split(',')[0] + data_value[0].strip().split(',')[1])
        except IndexError: # Will fail on IndexError if tries to split '900' with a ',' in ['',900]
            mileage_km = int(data_value[0].strip())
    
    return mileage_km

def mileage_retrieval(parsed_listing_url):
        
    data_value = parsed_listing_url.find_all(class_='row_info')[0].text.strip()
    data_value = data_value.split('km')
    mileage_km = mileage_error_handler(data_value)
    
    return mileage_km

# Manufactured Year Retriever
def manufactured_year_retrieval(parsed_listing_url):
    manufactured_year = parsed_listing_url.find_all(class_='row_info')[6].text.strip()
    return manufactured_year.split()[0]

# Transmission Retriever
def transmission_retrieval(parsed_listing_url):
    transmission = parsed_listing_url.find_all(class_='row_info')[7].text.strip()
    return transmission.split()[0]

# Deregistration Value Retriever
def dereg_value_retrieval(parsed_listing_url):
    # Splits into ['NA'], or ['$11,026', 'as', 'of', 'today', '(change)'] or ['$900', 'as', 'of', 'today', '(change)']
    data_value = parsed_listing_url.find_all(class_='row_info')[2].text.strip().split() 
    
    dereg_value_from_scrape_date = dereg_value_error_handler(data_value)
    return dereg_value_from_scrape_date
    

def dereg_value_error_handler(data_value):
    if len(data_value) < 2:  # Deals with ['NA'] scenario
        dereg_value_from_scrape_date = np.nan

    else: 
        data_value = data_value[0].split('$')[1] # Puts input into '11,026' or '900' format
        try:                 
            dereg_value_from_scrape_date = \
            int(data_value.split(',')[0] +\
                data_value.split(',')[1]) # Will fail on IndexError if tries to split '900' with a ',' in ['',900]
        except IndexError: 
            dereg_value_from_scrape_date = int(data_value.strip())

        return dereg_value_from_scrape_date


# Open Market Value Retriever
def omv_error_handler(data_value):
    if len(data_value) < 2:  # deals iwth ['NA'] input
        omv = np.nan

    else:
        try:
            omv = int(data_value[1].split(',')[0] +\
                      data_value[1].split(',')[1])  # Will fail on index error if try to split 900
        except IndexError:
            omv = int(data_value[1])
    return omv


def omv_retrieval(parsed_listing_url):    
    data_value = parsed_listing_url.find_all(class_='row_info')[8].text.split('$') 
    # Splits data into ['', '21,967'], ['','900'] or ['NA'] format for input into error function
    
    omv = omv_error_handler(data_value)
    return omv     

# ARF Retriever
def error_handler(data_value):
    if len(data_value) < 2:  # deals iwth ['NA'] input
        desired_value = np.nan

    else:
        try:
            desired_value = int(data_value[1].split(',')[0] +\
                                data_value[1].split(',')[1])   # Will fail on index error if try to split 900
        except IndexError:
            desired_value = int(data_value[1])
    return desired_value


def arf_retrieval(parsed_listing_url):
    data_value = parsed_listing_url.find_all(class_='row_info')[9].text.split('$')
    arf = error_handler(data_value)
    return arf

# COE Price retriever 
def coe_error_handler(data_value):
    if len(data_value) < 2:  # deals iwth ['NA'] input
        coe_from_scrape_date = np.nan

    else:
        try:
            coe_from_scrape_date = int(data_value[1].split(',')[0] +\
                                       data_value[1].split(',')[1])  # Will fail on index error if try to split 900
        except IndexError:
            coe_from_scrape_date = int(data_value[1])
    return coe_from_scrape_date


def coe_retrieval(parsed_listing_url):
    data_value = parsed_listing_url.find_all(class_='row_info')[3].text.split('$')
    coe_from_scrape_date = coe_error_handler(data_value)
    return coe_from_scrape_date

# Engine Capacity Retriever
def engine_capacity_error_handler(data_value):
    if len(data_value) < 2:  # deals iwth ['NA'] input
        desired_value = np.nan

    else:
        try:
            desired_value = int(data_value[0].split(',')[0] +\
                                       data_value[0].split(',')[1])  # Will fail on index error if try to split 900
        except IndexError:
            desired_value = int(data_value[0])
    return desired_value


def engine_capacity_retrieval(parsed_listing_url):
    data_value = parsed_listing_url.find_all(class_='row_info')[4].text.strip().split('cc')
    engine_capacity = engine_capacity_error_handler(data_value)
    return engine_capacity

# Curb Weight Retriever
def curb_weight_error_handler(data_value):
    if len(data_value) < 2:  # deals iwth ['NA'] input
        desired_value = np.nan

    else:
        try:
            desired_value = int(data_value[0].split(',')[0] +\
                                       data_value[0].split(',')[1])  # Will fail on index error if try to split 900
        except IndexError:
            desired_value = int(data_value[0])
    return desired_value


def curb_weight_retrieval(parsed_listing_url):
    data_value = parsed_listing_url.find_all(class_='row_info')[5].text.split()
    curb_weight = curb_weight_error_handler(data_value)
    return curb_weight

# Number of owners retriever
def number_of_owners_retrieval(parsed_listing_url):
    no_of_owners = int(parsed_listing_url.find_all(class_='row_info')[-1].text)
    return no_of_owners


# Type of Vehicle Retriever
def type_of_vehicle_retrieval(parsed_listing_url):
    type_of_vehicle = parsed_listing_url.find(class_='row_bg1').find_all('a')[0].text 
    return type_of_vehicle

## 4. Get Links For All Postings

Links for all the car postings will be stored in a list before accessing them one by one for data extraction

In [13]:
# Create listings URLs to iterate through
main_page_listing_list = [] # create list to store search pages
for idx, link in enumerate(range(3)):
    url = "https://www.sgcarmart.com/used_cars/listing.php?BRSR=" + str(idx * 100) + "&RPG=100&AVL=2&VEH=2" #search by of 100 car listings per page
    main_page_listing_list.append(url)

In [14]:
print(main_page_listing_list,'\n','\n', len(main_page_listing_list))

['https://www.sgcarmart.com/used_cars/listing.php?BRSR=0&RPG=100&AVL=2&VEH=2', 'https://www.sgcarmart.com/used_cars/listing.php?BRSR=100&RPG=100&AVL=2&VEH=2', 'https://www.sgcarmart.com/used_cars/listing.php?BRSR=200&RPG=100&AVL=2&VEH=2'] 
 
 3


## 5. Retrieval of Individual Listing URLs from Search Pages

In [15]:
# Base url, or you can think of this as the individual car listing prefix
base_url = 'https://www.sgcarmart.com/used_cars/'
listing_urls = []

# Acquiring indvidual car listings    
for main_link in main_page_listing_list:
   
    # Make a request to the website and get the object
    content = requests.get(main_link)

    # Parse the HTML text
    soup = BeautifulSoup(content.text, 'lxml')

    # Find every single URL in the webpage , refer to this post: # https://stackoverflow.com/questions/46490626/getting-all-links-from-a-page-beautiful-soup
    # This returns a list of every tag that contains a link in one main link (each element in main page listing)
    links = soup.find_all('a')
    
    # Create a list for storing all the individual listing urls
    
    for link in links:
        # Get link in <a href>
        suffix = link.get('href')

        # Check if 'ID=' and 'DL=' exist in the string
        if ('ID=' in suffix) and ('DL=' in suffix):

            # Concatenate the two strings if they do
            listing_url = base_url + suffix
        #    print(listing_url)
            
            # Append result to the list
            listing_urls.append(listing_url)
            
#     Removing duplicates
    set_listing_urls = set(listing_urls)
    listing_urls = list(set_listing_urls)
    
    # Prevent oneself from getting blocked from the website
    time.sleep(3)

In [16]:
print(len(listing_urls))
print(len(set(listing_urls)))
print(len(list(set(listing_urls))))

300
300
300


In [17]:
print(listing_urls[:10])

['https://www.sgcarmart.com/used_cars/info.php?ID=1288411&DL=3495&utm_content=SLeligible', 'https://www.sgcarmart.com/used_cars/info.php?ID=1292190&DL=4721&utm_content=SLeligible', 'https://www.sgcarmart.com/used_cars/info.php?ID=1327097&DL=3989&utm_content=SLeligible', 'https://www.sgcarmart.com/used_cars/info.php?ID=1253217&DL=4721&utm_content=SLeligible', 'https://www.sgcarmart.com/used_cars/info.php?ID=1263905&DL=4721&utm_content=SLeligible', 'https://www.sgcarmart.com/used_cars/info.php?ID=1333352&DL=3649&utm_content=SLeligible', 'https://www.sgcarmart.com/used_cars/info.php?ID=1323657&DL=4697&utm_content=SLeligible', 'https://www.sgcarmart.com/used_cars/info.php?ID=1333228&DL=3597', 'https://www.sgcarmart.com/used_cars/info.php?ID=1333232&DL=1360&utm_content=SLeligible', 'https://www.sgcarmart.com/used_cars/info.php?ID=1333276&DL=4412']


## 6. Create DataFrame

In [18]:
# Creating an empty DataFrame for attributes of interest
df = pd.DataFrame(columns=['LISTING_URL', 'BRAND', 'PRICE', 'DEPRE_YEARLY',
       'REG_DATE', 'MILEAGE_KM', 'MANUFACTURED_YEAR',
       'ROAD_TAX_YEARLY','TRANSMISSION', 'DEREG_VALUE_FROM_SCRAPE_DATE',
       'SCRAPE_DATE', 'OMV', 'ARF', 'COE_FROM_SCRAPE_DATE',
       'DAYS_OF_COE_LEFT', 'ENGINE_CAPACITY_CC', 'CURB_WEIGHT_KG',
       'NO_OF_OWNERS', 'VEHICLE_TYPE'])

In [20]:
filename = 'sgcarmart_used_cars_prices'
i = 0 # Indexing rows in the DF

for listingurl in listing_urls:
    response = requests.get(listingurl)
    listing_url = BeautifulSoup(response.text, 'lxml')
    
    print(listing_url)

    # Retrieval functions to pull data from the Individual Listings after they have been parsed
    df.loc[i, 'LISTING_URL'] = listingurl
    df.loc[i, 'BRAND'] = brand_retrieval(listing_url)
    df.loc[i, 'PRICE'] = price_retrieval(listing_url)
    try:
        df.loc[i, 'DEPRE_YEARLY'] = depreciation_yearly_retrieval(listing_url)
    except:
        df.loc[i, 'DEPRE_YEARLY'] = np.nan
        
    try:
        df.loc[i, 'REG_DATE'] = reg_date_retrieval(listing_url)
    except:
        df.loc[i, 'REG_DATE'] = np.nan
    
    try:
        df.loc[i, 'MILEAGE_KM'] = mileage_retrieval(listing_url)
    except:
        df.loc[i, 'MILEAGE_KM'] = np.nan

    try:
        df.loc[i, 'MANUFACTURED_YEAR'] = manufactured_year_retrieval(listing_url)
    except: 
        df.loc[i, 'MANUFACTURED_YEAR'] = np.nan
    
    try:
        df.loc[i, 'ROAD_TAX_YEARLY'] = road_tax_retrieval(listing_url)
    except:
        df.loc[i, 'ROAD_TAX_YEARLY'] = np.nan
        
    try:
        df.loc[i, 'TRANSMISSION'] = transmission_retrieval(listing_url)
    except:
        df.loc[i, 'TRANSMISSION'] = np.nan

        
    try:
        df.loc[i, 'DEREG_VALUE_FROM_SCRAPE_DATE'] = dereg_value_retrieval(listing_url)
    except: 
        df.loc[i, 'DEREG_VALUE_FROM_SCRAPE_DATE'] = np.nan
        
    df.loc[i, 'SCRAPE_DATE'] = datetime.now().strftime("%d/%m/%Y")
    
    try:
        df.loc[i, 'OMV'] = omv_retrieval(listing_url)
    except: 
        df.loc[i, 'OMV'] = np.nan

    try:
        df.loc[i, 'ARF'] = arf_retrieval(listing_url)
    except: 
        df.loc[i, 'ARF'] = np.nan
        
    try:
        df.loc[i, 'COE_FROM_SCRAPE_DATE'] = coe_retrieval(listing_url)
    except:
        df.loc[i, 'COE_FROM_SCRAPE_DATE'] = np.nan
        
    try:
        df.loc[i, 'DAYS_OF_COE_LEFT'] = days_of_coe_retrieval(listing_url)
    except:
        df.loc[i, 'DAYS_OF_COE_LEFT'] = np.nan
        
    try:
        df.loc[i, 'ENGINE_CAPACITY_CC'] = engine_capacity_retrieval(listing_url)
    except: 
        df.loc[i, 'ENGINE_CAPACITY_CC'] = np.nan
        
    try:
        df.loc[i, 'CURB_WEIGHT_KG'] = curb_weight_retrieval(listing_url)
    except:
        df.loc[i, 'CURB_WEIGHT_KG'] = np.nan
        
    try:
        df.loc[i, 'NO_OF_OWNERS'] = number_of_owners_retrieval(listing_url)
    except:
        df.loc[i, 'NO_OF_OWNERS'] = np.nan
        
    try:
        df.loc[i, 'VEHICLE_TYPE'] = type_of_vehicle_retrieval(listing_url)
    except:
        df.loc[i, 'VEHICLE_TYPE'] = np.nan
        
    df.to_csv("{}.csv".format(filename))    
        
    i += 1 # Allows next car listing to be put into a next row in the dataframe
    time.sleep(5)  # Prevents us from getting locked out of the website
    

<!DOCTYPE html PUBLIC "-//W3C//DTD XHTML 1.0 Transitional//EN" "http://www.w3.org/TR/xhtml1/DTD/xhtml1-transitional.dtd">
<html xmlns="http://www.w3.org/1999/xhtml">
<head>
<meta content="IE=Edge" http-equiv="X-UA-Compatible"/>
<title>Used 2017 Chevrolet Orlando 1.4A Turbo for Sale | AutoGuru+ SG LLP - Sgcarmart    </title>
<meta content="Latest price, photos &amp; features of Used 2017  Chevrolet Orlando 1.4A Turbo for sale by AutoGuru+ SG LLP in Singapore. The Only Place For Smart Car Buyers." property="og:description"/>
<meta content="Latest price, photos &amp; features of Used 2017  Chevrolet Orlando 1.4A Turbo for sale by AutoGuru+ SG LLP in Singapore. The Only Place For Smart Car Buyers." name="description"/>
<meta content="Used Chevrolet, Used Chevrolet Orlando, Used Chevrolet car, Used Chevrolet cars, Used car, Used cars, Used car dealer, Used car dealers, Used cars Singapore, Used car Singapore, Singapore used cars, Singapore used car, Used car classifieds, Used car classified

KeyboardInterrupt: 

In [ ]:
df = pd.read_csv('sgcarmart_used_cars_prices.csv',index_col=0)
df

LISTING_URL  \
0    https://www.sgcarmart.com/used_cars/info.php?I...   
1    https://www.sgcarmart.com/used_cars/info.php?I...   
2    https://www.sgcarmart.com/used_cars/info.php?I...   
3    https://www.sgcarmart.com/used_cars/info.php?I...   
4    https://www.sgcarmart.com/used_cars/info.php?I...   
..                                                 ...   
589  https://www.sgcarmart.com/used_cars/info.php?I...   
590  https://www.sgcarmart.com/used_cars/info.php?I...   
591  https://www.sgcarmart.com/used_cars/info.php?I...   
592  https://www.sgcarmart.com/used_cars/info.php?I...   
593  https://www.sgcarmart.com/used_cars/info.php?I...   

                                            BRAND     PRICE  DEPRE_YEARLY  \
0                        BMW X6 xDrive35i Sunroof  109800.0       30010.0   
1               Mazda 6 Wagon 2.5A Luxury Sunroof   70588.0       14830.0   
2                                    BMW M4 Coupe  270000.0       26990.0   
3                              Kia Cerato 1.6A LX   57333.0       12080.0   
4                 MG HS 1.5A Turbo Panoramic Roof  109800.0       15320.0   
..                                            ...       ...           ...   
589  Mercedes-Benz GLA-Class GLA180 Urban Edition  118000.0       17570.0   
590                            Toyota Wish 1.8A X   53800.0       15570.0   
591                          Audi A6 2.0A TFSI MU  139800.0       13970.0   
592                   Mercedes-Benz S-Class S400L  206000.0       20590.0   
593                          BMW 5 Series 525i XL   45800.0        9830.0   

        REG_DATE  MILEAGE_KM MANUFACTURED_YEAR  ROAD_TAX_YEARLY TRANSMISSION  \
0    20-Sep-2016    152000.0              2016           2362.0         Auto   
1    24-Jul-2018     56000.0              2018           1786.0         Auto   
2    30-Sep-2014         NaN              2014           2362.0         Auto   
3    14-Dec-2018     28188.0              2018            238.0         Auto   
4    16-Mar-2021     91000.0              2020            680.0         Auto   
..           ...         ...               ...              ...          ...   
589  13-Aug-2020         NaN              2019            740.0         Auto   
590  21-Jun-2017    118000.0              2016            974.0         Auto   
591  08-Dec-2014         NaN              2014           1194.0         Auto   
592  06-Feb-2015    165065.0              2014           2382.0         Auto   
593  25-Jun-2009    153000.0              2009           2694.0         Auto   

     DEREG_VALUE_FROM_SCRAPE_DATE SCRAPE_DATE      OMV       ARF  \
0                         69974.0  03/09/2024  69405.0   96929.0   
1                         28889.0  03/09/2024  24217.0   25904.0   
2                             NaN  03/09/2024  80431.0  116776.0   
3                         11528.0  03/09/2024  11238.0   11238.0   
4                         44584.0  03/09/2024  19426.0   19426.0   
..                            ...         ...      ...       ...   
589                       40039.0  03/09/2024  25170.0   27238.0   
590                       26878.0  03/09/2024  20412.0   20577.0   
591                           NaN  03/09/2024  38503.0   40905.0   
592                           NaN  03/09/2024  96954.0  146518.0   
593                       16493.0  03/09/2024  52627.0   52627.0   

     COE_FROM_SCRAPE_DATE  DAYS_OF_COE_LEFT  ENGINE_CAPACITY_CC  \
0                 58201.0             736.0              2979.0   
1                 31000.0            1095.0              2488.0   
2                     NaN               0.0              2979.0   
3                  8556.0            1550.0              1591.0   
4                 47506.0            2372.0              1490.0   
..                    ...               ...                 ...   
589               33000.0            1864.0              1595.0   
590               52000.0            1007.0              1797.0   
591                   NaN               